#### imports

In [1]:
import numpy as np
import pandas as pd 
import statsmodels.api as sm
import statsmodels.formula.api as smf
import seaborn as sns
from sklearn.preprocessing import scale 
from sklearn.model_selection import train_test_split, GridSearchCV, cross_val_score
from sklearn.metrics import confusion_matrix, accuracy_score, classification_report
from sklearn.metrics import roc_auc_score,roc_curve
import statsmodels.formula.api as smf
import matplotlib.pyplot as plt
from sklearn.neighbors import KNeighborsClassifier
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.naive_bayes import GaussianNB
from sklearn import tree
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import GradientBoostingClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from catboost import CatBoostClassifier

from warnings import filterwarnings
filterwarnings('ignore')

# Gradient Boosting Machines

## Model ve Tahmin

In [2]:
diabetes = pd.read_csv("diabetes.csv")
df = diabetes.copy()
df = df.dropna()
y = df["Outcome"]
X = df.drop(['Outcome'], axis=1)
X_train, X_test, y_train, y_test = train_test_split(X, y, 
                                                    test_size=0.30, 
                                                    random_state=42)

In [3]:
from sklearn.ensemble import GradientBoostingClassifier

In [4]:
gbm_model = GradientBoostingClassifier().fit(X_train, y_train)

In [5]:
y_pred = gbm_model.predict(X_test)
accuracy_score(y_test, y_pred)

0.7445887445887446

## Model Tuning

In [6]:
gbm_model.get_params()

{'ccp_alpha': 0.0,
 'criterion': 'friedman_mse',
 'init': None,
 'learning_rate': 0.1,
 'loss': 'deviance',
 'max_depth': 3,
 'max_features': None,
 'max_leaf_nodes': None,
 'min_impurity_decrease': 0.0,
 'min_impurity_split': None,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'min_weight_fraction_leaf': 0.0,
 'n_estimators': 100,
 'n_iter_no_change': None,
 'random_state': None,
 'subsample': 1.0,
 'tol': 0.0001,
 'validation_fraction': 0.1,
 'verbose': 0,
 'warm_start': False}

In [7]:
?gbm_model

Type:        GradientBoostingClassifier
String form: GradientBoostingClassifier()
Length:      100
File:        ~/opt/anaconda3/lib/python3.9/site-packages/sklearn/ensemble/_gb.py
Docstring:  
Gradient Boosting for classification.

GB builds an additive model in a
forward stage-wise fashion; it allows for the optimization of
arbitrary differentiable loss functions. In each stage ``n_classes_``
regression trees are fit on the negative gradient of the
binomial or multinomial deviance loss function. Binary classification
is a special case where only a single regression tree is induced.

Read more in the :ref:`User Guide <gradient_boosting>`.

Parameters
----------
loss : {'deviance', 'exponential'}, default='deviance'
    The loss function to be optimized. 'deviance' refers to
    deviance (= logistic regression) for classification
    with probabilistic outputs. For loss 'exponential' gradient
    boosting recovers the AdaBoost algorithm.

learning_rate : float, default=0.1
    Learning 

n_estimators önemli

subsambple'da 1 olarak alıcaz ki bütün örnekleri alsın çünkü zaten az sayıda elemanımız var test-train setlerinde

min_samples_split düğümde kaç gözlem olmalı, çok ölmcül bir parametre değil

max_depth önemli

In [8]:
gbm_params = {"learning_rate" : [0.001, 0.01, 0.1, 0.05],
             "n_estimators": [100,500,100],
             "max_depth": [3,5,10],
             "min_samples_split": [2,5,10]}

In [12]:
gbm = GradientBoostingClassifier()

gbm_cv = GridSearchCV(gbm, gbm_params, cv = 10, n_jobs = -1, verbose = 2)

In [13]:
gbm_cv.fit(X_train, y_train)

Fitting 10 folds for each of 108 candidates, totalling 1080 fits


GridSearchCV(cv=10, estimator=GradientBoostingClassifier(), n_jobs=-1,
             param_grid={'learning_rate': [0.001, 0.01, 0.1, 0.05],
                         'max_depth': [3, 5, 10],
                         'min_samples_split': [2, 5, 10],
                         'n_estimators': [100, 500, 100]},
             verbose=2)

In [14]:
print("En iyi parametreler: " + str(gbm_cv.best_params_))

En iyi parametreler: {'learning_rate': 0.1, 'max_depth': 3, 'min_samples_split': 5, 'n_estimators': 100}


In [18]:
gbm = GradientBoostingClassifier(learning_rate = 0.1, 
                                 max_depth = 3,
                                min_samples_split = 5,
                                n_estimators = 100)

In [19]:
gbm_tuned =  gbm.fit(X_train,y_train)

In [20]:
y_pred = gbm_tuned.predict(X_test)
accuracy_score(y_test, y_pred)

0.7445887445887446

In [21]:
# derste gösterilen optimized parametrelerle daha iyi sonuç aldım accuracy'de, neden?

# XGBoost

## Model ve Tahmin

In [24]:
df = diabetes.copy()
df = df.dropna()
y = df["Outcome"]
X = df.drop(['Outcome'], axis=1)
#X = df["Pregnancies"]
X = pd.DataFrame(X)
X_train, X_test, y_train, y_test = train_test_split(X, y, 
                                                    test_size=0.30, 
                                                    random_state=42)

In [25]:
#!pip install xgboost
from xgboost import XGBClassifier

In [26]:
xgb_model = XGBClassifier().fit(X_train, y_train)

In [27]:
xgb_model

XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=0, num_parallel_tree=1, predictor='auto', random_state=0,
              reg_alpha=0, reg_lambda=1, ...)

In [28]:
y_pred = xgb_model.predict(X_test)
accuracy_score(y_test, y_pred)

0.7359307359307359

## Model Tuning

In [29]:
xgb_model

XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=0, num_parallel_tree=1, predictor='auto', random_state=0,
              reg_alpha=0, reg_lambda=1, ...)

In [30]:
?xgb_model

Type:        XGBClassifier
String form:
XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
           colsample_bylevel=1 <...> _parallel_tree=1, predictor='auto', random_state=0,
           reg_alpha=0, reg_lambda=1, ...)
File:        ~/opt/anaconda3/lib/python3.9/site-packages/xgboost/sklearn.py
Docstring:  
Implementation of the scikit-learn API for XGBoost classification.


Parameters
----------

    n_estimators : int
        Number of boosting rounds.

    max_depth :  Optional[int]
        Maximum tree depth for base learners.
    max_leaves :
        Maximum number of leaves; 0 indicates no limit.
    max_bin :
        If using histogram-based algorithm, maximum number of bins per feature
    grow_policy :
        Tree growing policy. 0: favor splitting at nodes closest to the node, i.e. grow
        depth-wise. 1: favor splitting at nodes with highest loss change.
    learning_rate : Optional[float]
        Boosting learning rate (xgb's "eta")
    verbosity : Opti

In [31]:
xgb_params = {
        'n_estimators': [100, 500, 1000, 2000],
        'subsample': [0.6, 0.8, 1.0],
        'max_depth': [3, 4, 5,6],
        'learning_rate': [0.1,0.01,0.02,0.05],
        "min_samples_split": [2,5,10]}

In [32]:
xgb = XGBClassifier()

xgb_cv_model = GridSearchCV(xgb, xgb_params, cv = 10, n_jobs = -1, verbose = 2)

In [33]:
xgb_cv_model.fit(X_train, y_train)

Fitting 10 folds for each of 576 candidates, totalling 5760 fits
[CV] END learning_rate=0.001, max_depth=3, min_samples_split=2, n_estimators=100; total time=   0.1s
[CV] END learning_rate=0.001, max_depth=3, min_samples_split=2, n_estimators=500; total time=   0.5s
[CV] END learning_rate=0.001, max_depth=3, min_samples_split=2, n_estimators=500; total time=   0.6s
[CV] END learning_rate=0.001, max_depth=3, min_samples_split=5, n_estimators=500; total time=   0.6s
[CV] END learning_rate=0.001, max_depth=3, min_samples_split=5, n_estimators=100; total time=   0.1s
[CV] END learning_rate=0.001, max_depth=3, min_samples_split=10, n_estimators=100; total time=   0.1s
[CV] END learning_rate=0.001, max_depth=3, min_samples_split=10, n_estimators=100; total time=   0.1s
[CV] END learning_rate=0.001, max_depth=3, min_samples_split=10, n_estimators=500; total time=   0.6s
[CV] END learning_rate=0.001, max_depth=3, min_samples_split=10, n_estimators=100; total time=   0.1s
[CV] END learning_rate

GridSearchCV(cv=10,
             estimator=XGBClassifier(base_score=None, booster=None,
                                     callbacks=None, colsample_bylevel=None,
                                     colsample_bynode=None,
                                     colsample_bytree=None,
                                     early_stopping_rounds=None,
                                     enable_categorical=False, eval_metric=None,
                                     gamma=None, gpu_id=None, grow_policy=None,
                                     importance_type=None,
                                     interaction_constraints=None,
                                     learning_rate=None, max_bin=None,
                                     max_c...
                                     max_leaves=None, min_child_weight=None,
                                     missing=nan, monotone_constraints=None,
                                     n_estimators=100, n_jobs=None,
                        

In [34]:
xgb_cv_model.best_params_

{'learning_rate': 0.02,
 'max_depth': 3,
 'min_samples_split': 2,
 'n_estimators': 100,
 'subsample': 0.6}

In [41]:
# final model

In [38]:
xgb = XGBClassifier(learning_rate = 0.02, 
                    max_depth = 3,
                    min_samples_split = 2,
                    n_estimators = 100,
                    subsample = 0.6)

In [39]:
xgb_tuned =  xgb.fit(X_train,y_train)

[13:35:28] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-10.9-x86_64-cpython-37/xgboost/src/learner.cc:627: 
Parameters: { "min_samples_split" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.




In [40]:
y_pred = xgb_tuned.predict(X_test)
accuracy_score(y_test, y_pred)

0.7575757575757576

# LightGBM

## Model ve Tahmin

In [42]:
df = diabetes.copy()
df = df.dropna()
y = df["Outcome"]
X = df.drop(['Outcome'], axis=1)
#X = df["Pregnancies"]
X = pd.DataFrame(X)
X_train, X_test, y_train, y_test = train_test_split(X, y, 
                                                    test_size=0.30, 
                                                    random_state=42)

In [43]:
#!conda install -c conda-forge lightgbm
from lightgbm import LGBMClassifier

In [44]:
lgbm_model = LGBMClassifier().fit(X_train, y_train)

In [45]:
y_pred = lgbm_model.predict(X_test)
accuracy_score(y_test, y_pred)

0.7229437229437229

In [46]:
## Model Tuning

In [49]:
lgbm_model.get_params()

{'boosting_type': 'gbdt',
 'class_weight': None,
 'colsample_bytree': 1.0,
 'importance_type': 'split',
 'learning_rate': 0.1,
 'max_depth': -1,
 'min_child_samples': 20,
 'min_child_weight': 0.001,
 'min_split_gain': 0.0,
 'n_estimators': 100,
 'n_jobs': -1,
 'num_leaves': 31,
 'objective': None,
 'random_state': None,
 'reg_alpha': 0.0,
 'reg_lambda': 0.0,
 'silent': 'warn',
 'subsample': 1.0,
 'subsample_for_bin': 200000,
 'subsample_freq': 0}

In [48]:
?lgbm_model

Type:           LGBMClassifier
String form:    LGBMClassifier()
File:           ~/opt/anaconda3/lib/python3.9/site-packages/lightgbm/sklearn.py
Docstring:      LightGBM classifier.
Init docstring:
Construct a gradient boosting model.

Parameters
----------
boosting_type : str, optional (default='gbdt')
    'gbdt', traditional Gradient Boosting Decision Tree.
    'dart', Dropouts meet Multiple Additive Regression Trees.
    'goss', Gradient-based One-Side Sampling.
    'rf', Random Forest.
num_leaves : int, optional (default=31)
    Maximum tree leaves for base learners.
max_depth : int, optional (default=-1)
    Maximum tree depth for base learners, <=0 means no limit.
learning_rate : float, optional (default=0.1)
    Boosting learning rate.
    You can use ``callbacks`` parameter of ``fit`` method to shrink/adapt learning rate
    in training using ``reset_parameter`` callback.
    Note, that this will ignore the ``learning_rate`` argument in training.
n_estimators : int, optional (de

In [50]:
lgbm_params = {
        'n_estimators': [100, 500, 1000, 2000],
        'subsample': [0.6, 0.8, 1.0],
        'max_depth': [3, 4, 5,6],
        'learning_rate': [0.1,0.01,0.02,0.05],
        "min_child_samples": [5,10,20]}

In [51]:
lgbm = LGBMClassifier()

lgbm_cv_model = GridSearchCV(lgbm, lgbm_params, 
                             cv = 10, 
                             n_jobs = -1, 
                             verbose = 2)



In [52]:
lgbm_cv_model.fit(X_train, y_train)

Fitting 10 folds for each of 576 candidates, totalling 5760 fits
[13:33:23] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-10.9-x86_64-cpython-37/xgboost/src/learner.cc:627: 
Parameters: { "min_samples_split" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[CV] END learning_rate=0.05, max_depth=5, min_samples_split=5, n_estimators=2000, subsample=0.6; total time=   1.6s
[13:33:25] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-10.9-x86_64-cpython-37/xgboost/src/learner.cc:627: 
Parameters: { "min_samples_split" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some paramete

GridSearchCV(cv=10, estimator=LGBMClassifier(), n_jobs=-1,
             param_grid={'learning_rate': [0.1, 0.01, 0.02, 0.05],
                         'max_depth': [3, 4, 5, 6],
                         'min_child_samples': [5, 10, 20],
                         'n_estimators': [100, 500, 1000, 2000],
                         'subsample': [0.6, 0.8, 1.0]},
             verbose=2)

In [53]:
lgbm_cv_model.best_params_

{'learning_rate': 0.05,
 'max_depth': 3,
 'min_child_samples': 20,
 'n_estimators': 100,
 'subsample': 0.6}

In [57]:
lgbm = LGBMClassifier(learning_rate = 0.05, 
                       max_depth = 3,
                       subsample = 0.6,
                       n_estimators = 100,
                       min_child_samples = 20)

In [58]:
lgbm_tuned = lgbm.fit(X_train,y_train)

In [59]:
y_pred = lgbm_tuned.predict(X_test)
accuracy_score(y_test, y_pred)

0.7489177489177489

In [60]:
# yine best_params_'dan daha iyi parametreler var, neden?

# CatBoost

## Model & Tahmin

In [61]:
df = diabetes.copy()
df = df.dropna()
y = df["Outcome"]
X = df.drop(['Outcome'], axis=1)
#X = df["Pregnancies"]
X = pd.DataFrame(X)
X_train, X_test, y_train, y_test = train_test_split(X, y, 
                                                    test_size=0.30, 
                                                    random_state=42)

In [62]:
#!pip install catboost
from catboost import CatBoostClassifier

In [65]:
cat_model = CatBoostClassifier().fit(X_train, y_train)

Learning rate set to 0.0079
0:	learn: 0.6879744	total: 2.1ms	remaining: 2.1s
1:	learn: 0.6843414	total: 3.32ms	remaining: 1.66s
2:	learn: 0.6805760	total: 5.44ms	remaining: 1.81s
3:	learn: 0.6765782	total: 6.97ms	remaining: 1.74s
4:	learn: 0.6720829	total: 8.36ms	remaining: 1.66s
5:	learn: 0.6681617	total: 9.96ms	remaining: 1.65s
6:	learn: 0.6641912	total: 11.2ms	remaining: 1.59s
7:	learn: 0.6602881	total: 12.6ms	remaining: 1.56s
8:	learn: 0.6562626	total: 13.5ms	remaining: 1.49s
9:	learn: 0.6528483	total: 14.6ms	remaining: 1.44s
10:	learn: 0.6487823	total: 15.6ms	remaining: 1.4s
11:	learn: 0.6454980	total: 16.9ms	remaining: 1.39s
12:	learn: 0.6418953	total: 17.9ms	remaining: 1.36s
13:	learn: 0.6374431	total: 19.1ms	remaining: 1.34s
14:	learn: 0.6339676	total: 20.2ms	remaining: 1.32s
15:	learn: 0.6304252	total: 21.2ms	remaining: 1.3s
16:	learn: 0.6266998	total: 22.3ms	remaining: 1.29s
17:	learn: 0.6237660	total: 23.5ms	remaining: 1.28s
18:	learn: 0.6204394	total: 24.5ms	remaining: 1.27

In [66]:
y_pred = cat_model.predict(X_test)
accuracy_score(y_test, y_pred)

0.7402597402597403

## Model Tuning

In [67]:
catb_params = {
    'iterations': [200,500],
    'learning_rate': [0.01,0.05, 0.1],
    'depth': [3,5,8] }

In [68]:
catb = CatBoostClassifier()
catb_cv_model = GridSearchCV(catb, catb_params, cv=5, n_jobs = -1, verbose = 2)
catb_cv_model.fit(X_train, y_train)
catb_cv_model.best_params_

Fitting 5 folds for each of 18 candidates, totalling 90 fits
[CV] END learning_rate=0.05, max_depth=5, min_child_samples=5, n_estimators=2000, subsample=0.8; total time=   0.6s
[CV] END learning_rate=0.05, max_depth=5, min_child_samples=5, n_estimators=2000, subsample=0.8; total time=   0.6s
[CV] END learning_rate=0.05, max_depth=5, min_child_samples=10, n_estimators=500, subsample=0.6; total time=   0.1s
[CV] END learning_rate=0.05, max_depth=5, min_child_samples=10, n_estimators=500, subsample=0.8; total time=   0.2s
[CV] END learning_rate=0.05, max_depth=5, min_child_samples=10, n_estimators=500, subsample=0.8; total time=   0.1s
[CV] END learning_rate=0.05, max_depth=5, min_child_samples=10, n_estimators=500, subsample=1.0; total time=   0.1s
[CV] END learning_rate=0.05, max_depth=5, min_child_samples=10, n_estimators=500, subsample=1.0; total time=   0.2s
[CV] END learning_rate=0.05, max_depth=5, min_child_samples=10, n_estimators=500, subsample=1.0; total time=   0.1s
[CV] END le

{'depth': 8, 'iterations': 200, 'learning_rate': 0.01}

In [69]:
catb_cv_model.best_params_

{'depth': 8, 'iterations': 200, 'learning_rate': 0.01}

In [72]:
catb = CatBoostClassifier(iterations = 200, 
                          learning_rate = 0.01, 
                          depth = 8)

catb_tuned = catb.fit(X_train, y_train)
y_pred = catb_tuned.predict(X_test)

0:	learn: 0.6863312	total: 5.5ms	remaining: 1.09s
1:	learn: 0.6811157	total: 8.64ms	remaining: 856ms
2:	learn: 0.6752970	total: 11.7ms	remaining: 765ms
3:	learn: 0.6697432	total: 14.6ms	remaining: 715ms
4:	learn: 0.6641758	total: 18.1ms	remaining: 707ms
5:	learn: 0.6576656	total: 20.6ms	remaining: 665ms
6:	learn: 0.6521870	total: 22.8ms	remaining: 630ms
7:	learn: 0.6465564	total: 24.9ms	remaining: 598ms
8:	learn: 0.6407595	total: 26.9ms	remaining: 570ms
9:	learn: 0.6357725	total: 29.1ms	remaining: 552ms
10:	learn: 0.6299942	total: 31.4ms	remaining: 539ms
11:	learn: 0.6240480	total: 33.3ms	remaining: 522ms
12:	learn: 0.6196095	total: 35.4ms	remaining: 510ms
13:	learn: 0.6148715	total: 37.4ms	remaining: 497ms
14:	learn: 0.6092626	total: 39.4ms	remaining: 486ms
15:	learn: 0.6046764	total: 41.4ms	remaining: 477ms
16:	learn: 0.6012725	total: 43.3ms	remaining: 466ms
17:	learn: 0.5958121	total: 45.2ms	remaining: 457ms
18:	learn: 0.5903243	total: 47ms	remaining: 448ms
19:	learn: 0.5866024	tota

In [73]:
y_pred = catb_tuned.predict(X_test)
accuracy_score(y_test, y_pred)

0.7532467532467533

95:	learn: 0.3786339	total: 364ms	remaining: 1.53s
96:	learn: 0.3769260	total: 367ms	remaining: 1.53s
97:	learn: 0.3750357	total: 373ms	remaining: 1.53s
98:	learn: 0.3736794	total: 376ms	remaining: 1.52s
99:	learn: 0.3724135	total: 378ms	remaining: 1.51s
100:	learn: 0.3710033	total: 380ms	remaining: 1.5s
101:	learn: 0.3697246	total: 382ms	remaining: 1.49s
102:	learn: 0.3684121	total: 384ms	remaining: 1.48s
103:	learn: 0.3670108	total: 385ms	remaining: 1.47s
104:	learn: 0.3657805	total: 389ms	remaining: 1.46s
105:	learn: 0.3645533	total: 391ms	remaining: 1.45s
106:	learn: 0.3629460	total: 393ms	remaining: 1.44s
107:	learn: 0.3608001	total: 394ms	remaining: 1.43s
108:	learn: 0.3596995	total: 397ms	remaining: 1.42s
109:	learn: 0.3581543	total: 398ms	remaining: 1.41s
110:	learn: 0.3566672	total: 403ms	remaining: 1.41s
111:	learn: 0.3553716	total: 405ms	remaining: 1.4s
112:	learn: 0.3541971	total: 409ms	remaining: 1.4s
113:	learn: 0.3521533	total: 411ms	remaining: 1.39s
114:	learn: 0.350737